<a href="https://colab.research.google.com/github/yaolihua081/Stanford-CS06dataviz/blob/main/CS06HW8_GeoPlot.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

CS06 HW8

Geo Map using SEx_Age_state data, has deaths from different causes, including Covid-19

In [11]:
#
import seaborn as sns

import sys, platform, numpy as np, nltk, re, sklearn, pandas as pd, seaborn as sns, collections


import matplotlib.pyplot as plt
import hashlib
import matplotlib.style as style
style.use('fivethirtyeight')

import altair as alt
#https://data.cdc.gov/NCHS/Provisional-COVID-19-Death-Counts-by-Sex-Age-and-S/9bhg-hcku
import folium

In [13]:
#!pip install kaggle
from google.colab import files
files.upload()

Saving meteorite-landings.csv to meteorite-landings.csv


{'meteorite-landings.csv': b'name,id,nametype,recclass,mass,fall,year,reclat,reclong,GeoLocation\r\nAachen,1,Valid,L5,21,Fell,1880,50.775000,6.083330,"(50.775000, 6.083330)"\r\nAarhus,2,Valid,H6,720,Fell,1951,56.183330,10.233330,"(56.183330, 10.233330)"\r\nAbee,6,Valid,EH4,107000,Fell,1952,54.216670,-113.000000,"(54.216670, -113.000000)"\r\nAcapulco,10,Valid,Acapulcoite,1914,Fell,1976,16.883330,-99.900000,"(16.883330, -99.900000)"\r\nAchiras,370,Valid,L6,780,Fell,1902,-33.166670,-64.950000,"(-33.166670, -64.950000)"\r\nAdhi Kot,379,Valid,EH4,4239,Fell,1919,32.100000,71.800000,"(32.100000, 71.800000)"\r\nAdzhi-Bogdo (stone),390,Valid,LL3-6,910,Fell,1949,44.833330,95.166670,"(44.833330, 95.166670)"\r\nAgen,392,Valid,H5,30000,Fell,1814,44.216670,0.616670,"(44.216670, 0.616670)"\r\nAguada,398,Valid,L6,1620,Fell,1930,-31.600000,-65.233330,"(-31.600000, -65.233330)"\r\nAguila Blanca,417,Valid,L,1440,Fell,1920,-30.866670,-64.550000,"(-30.866670, -64.550000)"\r\nAioun el Atrouss,423,Valid,Diog

Altair to plot Geo map

In [5]:
#This data has state ID and state name
from vega_datasets import data
source = data.population_engineers_hurricanes()
source
states = alt.topo_feature(data.us_10m.url, 'states')
states

UrlData({
  format: TopoDataFormat({
    feature: 'states',
    type: 'topojson'
  }),
  url: 'https://vega.github.io/vega-datasets/data/us-10m.json'
})

In [6]:
Sex_age_state_data=pd.read_csv('Provisional_COVID-19_Death_Counts_by_Sex__Age__and_StateNov17.csv')
Sex_age_state_data.dropna()

Empty DataFrame
Columns: [Data as of, Start week, End Week, State, Sex, Age group, COVID-19 Deaths, Total Deaths, Pneumonia Deaths, Pneumonia and COVID-19 Deaths, Influenza Deaths, Pneumonia, Influenza, or COVID-19 Deaths, Footnote]
Index: []

In [7]:
Sex_age_state_data.head()

Data as of  Start week  ... Pneumonia, Influenza, or COVID-19 Deaths Footnote
0  11/12/2020  02/01/2020  ...                                 356777.0      NaN
1  11/12/2020  02/01/2020  ...                                    169.0      NaN
2  11/12/2020  02/01/2020  ...                                    605.0      NaN
3  11/12/2020  02/01/2020  ...                                    144.0      NaN
4  11/12/2020  02/01/2020  ...                                    199.0      NaN

[5 rows x 13 columns]

In [8]:
Sex_age_state_subset=Sex_age_state_data[['State', 'Sex','Age group','COVID-19 Deaths','Total Deaths','Influenza Deaths','Pneumonia Deaths']]
filter=Sex_age_state_data['Sex']=='All Sexes'
Sex_age_state_data_sub=Sex_age_state_data[filter]
filter=Sex_age_state_data_sub['Age group']=='All Ages'
Sex_age_state_data_sub_sub=Sex_age_state_data_sub[filter]
Sex_age_state_subset_sorted=Sex_age_state_data_sub_sub.sort_values(by='State')
source_sorted=source.sort_values(by='state')
source_sorted
Sex_age_state_subset_sorted['state']=Sex_age_state_subset_sorted['State']
Sex_age_state_subset_sorted.drop(['State'],axis = 1, inplace=True)

Sex_age_state_subset_sorted
all_state_data=pd.merge(Sex_age_state_subset_sorted,source_sorted)
all_state_data.head()


Data as of  Start week    End Week  ... population engineers  hurricanes
0  11/12/2020  02/01/2020  11/07/2020  ...    4863300  0.003422          22
1  11/12/2020  02/01/2020  11/07/2020  ...     741894  0.001591           0
2  11/12/2020  02/01/2020  11/07/2020  ...    6931071  0.004774           0
3  11/12/2020  02/01/2020  11/07/2020  ...    2988248  0.002440           0
4  11/12/2020  02/01/2020  11/07/2020  ...   39250017  0.007126           0

[5 rows x 17 columns]

In [9]:
bar1=alt.Chart(states, title="USA State Death Distributions by Nov 17, 2020").mark_geoshape().encode(
            alt.Color('COVID-19 Deaths', type='quantitative'),
            tooltip=['state:N',
                 alt.Tooltip('COVID-19 Deaths:Q'),
                 alt.Tooltip('Pneumonia Deaths:Q'),
                 alt.Tooltip('Influenza Deaths:Q'),
                 alt.Tooltip('Total Deaths:Q')]
    ).transform_lookup(
        lookup='id',
        from_=alt.LookupData(all_state_data, 'id', ['state', 'Age group','COVID-19 Deaths','Total Deaths','Pneumonia Deaths','Influenza Deaths'])
    ).properties(
        width=500,
        height=300
    ).project(
        type='albersUsa'
)
combined=bar1
combined.save('USA_Covid_Geo.html')
from google.colab import files
files.download('USA_Covid_Geo.html')
combined

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

alt.Chart(...)

Folium to plot Geo map

In [14]:
#covid19_by_country = pd.read_csv('https://github.com/owid/covid-19-data/blob/master/public/data/owid-covid-data.csv')
United_States_Covid=pd.read_csv('United_States_COVIDNov17.csv')#https://data.cdc.gov/Case-Surveillance/United-States-COVID-19-Cases-and-Deaths-by-State-o/9mfq-cb36

USAStateABV_data=pd.read_csv('USAStateABV.csv')

In [32]:
United_States_Covid.head()

submission_date state  ...  consent_cases  consent_deaths
0      01/22/2020    MN  ...            NaN           Agree
1      01/23/2020    MN  ...            NaN           Agree
2      01/24/2020    MN  ...            NaN           Agree
3      01/25/2020    MN  ...            NaN           Agree
4      01/26/2020    MN  ...            NaN           Agree

[5 rows x 15 columns]

In [ ]:
United_States_Covid.dropna()
United_States_Covid.head()
United_state_sum=United_States_Covid.groupby(['state'])['new_case'].sum()

temp=pd.DataFrame(United_state_sum)
temp=pd.DataFrame(temp.index.tolist())

United_state_covid_case_data=pd.concat([temp,pd.DataFrame(United_state_sum.values)],axis=1).reindex(temp.index)

United_state_covid_case_data.columns=['State','total_cases']
United_state_covid_case_data.head


In [40]:

url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
state_geo = f'{url}/us-states.json'

m = folium.Map(location=[48, -102], zoom_start=3)

folium.Choropleth(
    geo_data=state_geo,
    name='choropleth',
    data=United_state_covid_case_data,
    columns=['State', 'total_cases'],
    key_on='feature.id',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='USA Covid-19 Total Cases By State By Nov 17, 2020'
).add_to(m)

folium.LayerControl().add_to(m)

combined=m
combined.save('USA_Covid_Case_Foli.html')
from google.colab import files
files.download('USA_Covid_Case_Foli.html')
combined

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
United_States_Covid.head()
United_state_death_sum=United_States_Covid.groupby(['state'])['new_death'].sum()

temp=pd.DataFrame(United_state_death_sum)
temp=pd.DataFrame(temp.index.tolist())

United_state_covid_death_data=pd.concat([temp,pd.DataFrame(United_state_death_sum.values)],axis=1).reindex(temp.index)

United_state_covid_death_data.columns=['State','total_death']
United_state_covid_death_data.head



In [42]:
url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
state_geo = f'{url}/us-states.json'

m = folium.Map(location=[48, -102], zoom_start=3)

folium.Choropleth(
    geo_data=state_geo,
    name='choropleth',
    data=United_state_covid_death_data,
    columns=['State', 'total_death'],
    key_on='feature.id',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='USA Covid-19 Total Deaths By State By Nov 17, 2020'
).add_to(m)

folium.LayerControl().add_to(m)

combined=m
combined.save('USA_Covid_Death_Folium.html')
from google.colab import files
files.download('USA_Covid_Death_Folium.html')
combined

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

From Banu

In [43]:
meteorite=pd.read_csv("meteorite-landings.csv")
meteorite.loc[meteorite['mass'].idxmax()] #The max value-- mass of a meteor

name                              Hoba
id                               11890
nametype                         Valid
recclass                     Iron, IVB
mass                             6e+07
fall                             Found
year                              1920
reclat                        -19.5833
reclong                        17.9167
GeoLocation    (-19.583330, 17.916670)
Name: 16383, dtype: object

In [44]:
# Let's make Hoba strike even more exciting by adding an educational video and a text

#Set the location of Hoba 
map_hoba = folium.Map(location=[-19.5833,17.9167],
                        tiles = "Stamen Terrain",
                    
                        zoom_start = 9)

# Add a Hyperlink about Hoba
folium.Marker([-19.5833,17.9167],
              popup='<a href="https://www.youtube.com/watch?v=eQcAxzZtBwc" target="_blank">Hoba</a>',
              icon=folium.Icon(color='green')
             ).add_to(map_hoba)


map_hoba